In [ ]:

import pandas as pd
import numpy as np
import os
import sys
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

# --- GitHub Token Setup ---
os.environ["GITHUB_TOKEN"] = "ghp_##############"

# --- Config ---
years = list(range(2010, 2026))
base_url = "https://raw.githubusercontent.com/blainehodder/WCSB_Supply_Demand/main/raw_data/st39/ST39-{}.xlsx"
sheet_name = "VAR0800-ST39Extracts_xls"

product_anchors = [
    "Oil Sands (tonnes)", "Synthetic Crude Oil  (m3)", "Diluent Naphtha (m3)",
    "Process Gas (103m3)", "Bitumen (m3)", "Electricity (MWh)", "Sulphur (tonnes)"
]

month_map = {
    "January": 1, "February": 2, "March": 3, "April": 4,
    "May": 5, "June": 6, "July": 7, "August": 8,
    "September": 9, "October": 10, "November": 11, "December": 12
}

# --- Clone and import GitHub push module ---
!git clone https://github.com/blainehodder/WCSB_Supply_Demand.git
sys.path.append("/content/WCSB_Supply_Demand")
from utils.github_commit import push_df_to_github

def is_operator_header(row, month_cols):
    """A header row is mostly NaNs in numeric columns and has a label in col 0"""
    return pd.notna(row[0]) and sum(pd.to_numeric(row[month_cols], errors='coerce').notna()) <= 3

def process_st39_year(year):
    url = base_url.format(year)
    df = pd.read_excel(url, sheet_name=sheet_name, header=None)

    blocks = []
    block_starts = [
        (i, str(row[0]).strip())
        for i, row in df.iterrows()
        if str(row[0]).strip() in product_anchors
    ]

    for idx, (start_idx, anchor) in enumerate(block_starts):
        end_idx = block_starts[idx + 1][0] if idx + 1 < len(block_starts) else len(df)

        try:
            header_row = df.iloc[start_idx + 1, 1:13].tolist()
            year_val = df.iloc[start_idx + 1, 13]
            header_row = [str(h).strip() for h in header_row]

            if any(pd.isna(header_row)) or pd.isna(year_val):
                continue

            block = df.iloc[start_idx + 2:end_idx, 0:14].copy()
            block.columns = ['Metric'] + header_row + ['Drop']
            block["Product"] = anchor
            block["Year"] = int(year_val)

            # Identify plant headers and forward-fill
            block["Is_Plant_Header"] = block.apply(lambda r: is_operator_header(r, header_row), axis=1)
            block["Plant"] = np.where(block["Is_Plant_Header"], block["Metric"], np.nan)
            block["Plant"] = block["Plant"].ffill()

            # Filter data rows (not headers)
            data_rows = block[~block["Is_Plant_Header"]].copy()

            # Melt
            melted = pd.melt(
                data_rows,
                id_vars=["Plant", "Product", "Metric", "Year"],
                value_vars=header_row,
                var_name="Month",
                value_name="Value"
            )

            melted["Month_Num"] = melted["Month"].map(month_map)
            melted["Date"] = pd.to_datetime(dict(year=melted["Year"], month=melted["Month_Num"], day=1))
            melted["Value"] = pd.to_numeric(melted["Value"], errors="coerce")
            melted = melted.dropna(subset=["Value"])

            blocks.append(melted)

        except Exception as e:
            print(f"⚠️ Skipping block {anchor} ({year}): {e}")

    return pd.concat(blocks, ignore_index=True) if blocks else None

# --- Loop and Combine ---
all_data = []
for y in years:
    print(f"📅 Processing {y}...")
    year_df = process_st39_year(y)
    if year_df is not None:
        all_data.append(year_df)

if not all_data:
    raise ValueError("❌ No ST39 data parsed.")

final_st39_df = pd.concat(all_data, ignore_index=True)
final_st39_df = final_st39_df.sort_values(by=["Date", "Plant", "Product"])

# --- Push to GitHub ---
push_df_to_github(
    df=final_st39_df,
    user="blainehodder",
    repo="WCSB_Supply_Demand",
    path="clean_data/st39/st39_cleaned.csv",
    commit_message="Upload cleaned ST39 data (with plant/metric separation)"
)

print("✅ Successfully processed and pushed ST39 data.")


Cloning into 'WCSB_Supply_Demand'...
remote: Enumerating objects: 172, done.
remote: Counting objects: 100% (172/172), done.
remote: Compressing objects: 100% (153/153), done.
remote: Total 172 (delta 45), reused 0 (delta 0), pack-reused 0 (from 0)
Receiving objects: 100% (172/172), 4.90 MiB | 5.89 MiB/s, done.
Resolving deltas: 100% (45/45), done.
📅 Processing 2010...


<ipython-input-1-f9e7ff913aee>:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  return pd.notna(row[0]) and sum(pd.to_numeric(row[month_cols], errors='coerce').notna()) <= 3
<ipython-input-1-f9e7ff913aee>:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  return pd.notna(row[0]) and sum(pd.to_numeric(row[month_cols], errors='coerce').notna()) <= 3
<ipython-input-1-f9e7ff913aee>:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  retur

📅 Processing 2011...


<ipython-input-1-f9e7ff913aee>:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  return pd.notna(row[0]) and sum(pd.to_numeric(row[month_cols], errors='coerce').notna()) <= 3
<ipython-input-1-f9e7ff913aee>:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  return pd.notna(row[0]) and sum(pd.to_numeric(row[month_cols], errors='coerce').notna()) <= 3
<ipython-input-1-f9e7ff913aee>:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  retur

📅 Processing 2012...


...

📅 Processing 2024...


<ipython-input-1-f9e7ff913aee>:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  return pd.notna(row[0]) and sum(pd.to_numeric(row[month_cols], errors='coerce').notna()) <= 3
<ipython-input-1-f9e7ff913aee>:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  return pd.notna(row[0]) and sum(pd.to_numeric(row[month_cols], errors='coerce').notna()) <= 3
<ipython-input-1-f9e7ff913aee>:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  retur

📅 Processing 2025...


<ipython-input-1-f9e7ff913aee>:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  return pd.notna(row[0]) and sum(pd.to_numeric(row[month_cols], errors='coerce').notna()) <= 3
<ipython-input-1-f9e7ff913aee>:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  return pd.notna(row[0]) and sum(pd.to_numeric(row[month_cols], errors='coerce').notna()) <= 3
<ipython-input-1-f9e7ff913aee>:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  retur

✅ File pushed to GitHub: https://github.com/blainehodder/WCSB_Supply_Demand/blob/main/clean_data/st39/st39_cleaned.csv
✅ Successfully processed and pushed ST39 data.


# New Section

In [ ]:
from google.colab import sheets
sheet = sheets.InteractiveSheet(df=final_df)

MessageError: Error: credential propagation was unsuccessful